In [1]:
import numpy as np
import json
import os
from matplotlib import pyplot as plt
import matplotlib.dates as mdates
from obspy import read,Stream, Trace
from obspy.core import UTCDateTime
import math as M
from matplotlib import mlab
from matplotlib.colors import Normalize
import requests
from lxml import html
from scipy import signal
from scipy import interpolate
from scipy import stats
import matplotlib.colors as colors
import datetime
from scipy import signal
import requests
import urllib
import datetime
import time as tm
import pandas as pd
import multiprocessing as mp
import function_lib as lib
import math
import pickle
import matplotlib

In [2]:
# wind data
def smoothen_data(L, data, win):
    if win == "rect":
        ma_filter = np.ones(L) / L
    elif win == "hann":
        if L % 2 == 0: L = L + 1
        ma_filter = signal.hann(L, True)
        ma_filter = ma_filter / np.sum(ma_filter)
    
    data_smooth = np.convolve(data, ma_filter, 'same')
        
    return data_smooth

def interpolate_del_list(del_list, len_data):
    for i in range(len(del_list)):
        if i == len(del_list) -1:
            if len_data - 1 - del_list[i] < 10:
                del_list.extend(np.arange(del_list[i] + 1, len_data, 1))
        elif i == 0:
            if del_list[i] < 10:
                del_list.extend(np.arange(0, i, 1))
        elif del_list[i+1] - del_list[i] < 10:
            del_list.extend(np.arange(del_list[i] + 1, del_list[i+1], 1))
    return del_list

In [3]:
## get URLs for mooring data
urls = lib.web_crawler_mooring('2015-05-01T00:00:00.000Z', '2020-02-20T12:00:00.000Z', location='offshore')

# get mooring data
print(urls)
data = lib.get_mooring_data(urls)

telemetered
{'requestUUID': 'ce751e2e-828c-4906-93d1-0e5031ee084b', 'outputURL': 'https://opendap.oceanobservatories.org/thredds/catalog/ooi/jhrag@uw.edu/20200716T183404565Z-CE04OSSM-SBD11-06-METBKA000-telemetered-metbk_a_dcl_instrument/catalog.html', 'allURLs': ['https://opendap.oceanobservatories.org/thredds/catalog/ooi/jhrag@uw.edu/20200716T183404565Z-CE04OSSM-SBD11-06-METBKA000-telemetered-metbk_a_dcl_instrument/catalog.html', 'https://opendap.oceanobservatories.org/async_results/jhrag@uw.edu/20200716T183404565Z-CE04OSSM-SBD11-06-METBKA000-telemetered-metbk_a_dcl_instrument'], 'sizeCalculation': 177918760, 'timeCalculation': 60, 'numberOfSubJobs': 64}


KeyboardInterrupt: 

In [4]:
# read file containing the clustered rain even
rain_dct = {}
for file in os.listdir('rain_data_offshore_events/'):
    rain_dct[file.split('_')[1].split('.')[0]] = pd.read_csv('rain_data_offshore_events/' + file )
    
#convert starttime and endtime to datetime objects
for key in rain_dct:
    for i in range(len(rain_dct[key])):
        pd.set_option('mode.chained_assignment','warn')
        rain_dct[key].starttime[i] = datetime.datetime.fromisoformat(rain_dct[key].starttime[i])
        rain_dct[key].endtime[i] = datetime.datetime.fromisoformat(rain_dct[key].endtime[i])

C:\Users\fschwock\AppData\Local\Continuum\anaconda3\envs\obspy\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
C:\Users\fschwock\AppData\Local\Continuum\anaconda3\envs\obspy\lib\site-packages\ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # This is added back by InteractiveShellApp.init_path()


In [59]:
# convert seconds to datetime
time = data.time
time = time.apply(lib.ntp_seconds_to_datetime)

# get wind data
wind_mag = np.sqrt((data.eastward_wind_velocity)**2 + (data.northward_wind_velocity)**2)
wind_angle = np.arctan2(data.northward_wind_velocity, data.eastward_wind_velocity)

time_diff = data.time.diff()

t = tm.time()

# remove time periods where sampling period changes
time_diff_s = data.time.diff()
del_list = [i for i in time_diff_s.index if time_diff_s[i] > 90 or time_diff_s[i] <= 0]
del_list = interpolate_del_list(del_list, len(time_diff_s))
for i in del_list:
    wind_mag[i] = np.nan
    wind_angle[i] = np.nan
    
# compute average wind speed and angle
wind_vec = wind_mag.values * np.exp(1j * wind_angle.values)
wind_vec_smooth = smoothen_data(21, wind_vec, 'hann')
wind_mag_smooth = abs(wind_vec_smooth)
wind_angle_smooth = np.angle(wind_vec_smooth)

# remove time periods where rain is present
cnt = 0
for key in rain_dct:
    for i in range(len(rain_dct[key])):
        try:
            idx = np.where(time == rain_dct[key].endtime[i])[0][0]
        except:
            sec = np.array([item.total_seconds() for item in time - rain_dct[key].endtime[i]])
            idx = np.where(abs(sec) < 10)[0][0]
        wind_mag[idx] = np.nan
        wind_angle[idx] = np.nan
    cnt += 1
    print('finished event ', key, '; ', cnt / len(rain_dct) * 100, '%')

finished event  0 ;  0.08032128514056225 %
finished event  1 ;  0.1606425702811245 %
finished event  10 ;  0.24096385542168677 %
finished event  100 ;  0.321285140562249 %
finished event  1000 ;  0.4016064257028112 %
finished event  1001 ;  0.48192771084337355 %
finished event  1002 ;  0.5622489959839357 %
finished event  1003 ;  0.642570281124498 %
finished event  1004 ;  0.7228915662650602 %
finished event  1005 ;  0.8032128514056224 %
finished event  1006 ;  0.8835341365461846 %
finished event  1007 ;  0.9638554216867471 %
finished event  1008 ;  1.0441767068273093 %
finished event  1009 ;  1.1244979919678715 %
finished event  101 ;  1.2048192771084338 %
finished event  1010 ;  1.285140562248996 %
finished event  1011 ;  1.3654618473895583 %
finished event  1012 ;  1.4457831325301205 %
finished event  1013 ;  1.5261044176706828 %
finished event  1014 ;  1.6064257028112447 %
finished event  1015 ;  1.6867469879518073 %
finished event  1016 ;  1.7670682730923692 %
finished event  1017

finished event  1164 ;  14.93975903614458 %
finished event  1165 ;  15.020080321285139 %
finished event  1166 ;  15.100401606425704 %
finished event  1167 ;  15.180722891566264 %
finished event  1168 ;  15.261044176706829 %
finished event  1169 ;  15.341365461847388 %
finished event  117 ;  15.421686746987953 %
finished event  1170 ;  15.502008032128515 %
finished event  1171 ;  15.582329317269075 %
finished event  1172 ;  15.66265060240964 %
finished event  1173 ;  15.7429718875502 %
finished event  1174 ;  15.823293172690764 %
finished event  1175 ;  15.903614457831324 %
finished event  1176 ;  15.98393574297189 %
finished event  1177 ;  16.06425702811245 %
finished event  1178 ;  16.14457831325301 %
finished event  1179 ;  16.224899598393574 %
finished event  118 ;  16.305220883534137 %
finished event  1180 ;  16.3855421686747 %
finished event  1181 ;  16.46586345381526 %
finished event  1182 ;  16.546184738955823 %
finished event  1183 ;  16.626506024096386 %
finished event  1184 ;

finished event  385 ;  45.30120481927711 %
finished event  386 ;  45.38152610441767 %
finished event  387 ;  45.46184738955824 %
finished event  388 ;  45.54216867469879 %
finished event  389 ;  45.622489959839356 %
finished event  39 ;  45.70281124497992 %
finished event  390 ;  45.78313253012048 %
finished event  391 ;  45.863453815261046 %
finished event  392 ;  45.94377510040161 %
finished event  393 ;  46.024096385542165 %
finished event  394 ;  46.10441767068273 %
finished event  395 ;  46.1847389558233 %
finished event  396 ;  46.265060240963855 %
finished event  397 ;  46.34538152610442 %
finished event  398 ;  46.42570281124498 %
finished event  399 ;  46.50602409638554 %
finished event  4 ;  46.58634538152611 %
finished event  40 ;  46.666666666666664 %
finished event  400 ;  46.74698795180723 %
finished event  401 ;  46.82730923694779 %
finished event  402 ;  46.907630522088354 %
finished event  403 ;  46.98795180722892 %
finished event  404 ;  47.06827309236948 %
finished e

finished event  557 ;  60.6425702811245 %
finished event  558 ;  60.722891566265055 %
finished event  559 ;  60.80321285140562 %
finished event  56 ;  60.88353413654618 %
finished event  560 ;  60.96385542168675 %
finished event  561 ;  61.044176706827315 %
finished event  562 ;  61.12449799196787 %
finished event  563 ;  61.204819277108435 %
finished event  564 ;  61.285140562249 %
finished event  565 ;  61.365461847389554 %
finished event  566 ;  61.44578313253012 %
finished event  567 ;  61.52610441767068 %
finished event  568 ;  61.606425702811244 %
finished event  569 ;  61.686746987951814 %
finished event  57 ;  61.76706827309238 %
finished event  570 ;  61.84738955823293 %
finished event  571 ;  61.9277108433735 %
finished event  572 ;  62.00803212851406 %
finished event  573 ;  62.088353413654616 %
finished event  574 ;  62.16867469879518 %
finished event  575 ;  62.24899598393574 %
finished event  576 ;  62.3293172690763 %
finished event  577 ;  62.409638554216876 %
finished e

finished event  73 ;  76.06425702811245 %
finished event  730 ;  76.144578313253 %
finished event  731 ;  76.22489959839356 %
finished event  732 ;  76.30522088353415 %
finished event  733 ;  76.3855421686747 %
finished event  734 ;  76.46586345381526 %
finished event  735 ;  76.54618473895583 %
finished event  736 ;  76.62650602409639 %
finished event  737 ;  76.70682730923694 %
finished event  738 ;  76.78714859437751 %
finished event  739 ;  76.86746987951807 %
finished event  74 ;  76.94779116465863 %
finished event  740 ;  77.0281124497992 %
finished event  741 ;  77.10843373493977 %
finished event  742 ;  77.18875502008032 %
finished event  743 ;  77.26907630522089 %
finished event  744 ;  77.34939759036145 %
finished event  745 ;  77.429718875502 %
finished event  746 ;  77.51004016064257 %
finished event  747 ;  77.59036144578313 %
finished event  748 ;  77.67068273092369 %
finished event  749 ;  77.75100401606426 %
finished event  75 ;  77.83132530120483 %
finished event  750 

...

finished event  30221  endtime =  2020-01-07T11:44:22.000000000
finished event  30222  endtime =  2020-01-07T12:44:46.000000000
finished event  30223  endtime =  2020-01-07T13:44:30.000000000
finished event  30224  endtime =  2020-01-07T14:44:22.000000000
finished event  30225  endtime =  2020-01-07T15:44:38.000000000
finished event  30226  endtime =  2020-01-07T16:44:30.000000000
finished event  30227  endtime =  2020-01-07T17:44:50.000000000
finished event  30228  endtime =  2020-01-07T18:44:35.000000000
finished event  30229  endtime =  2020-01-07T19:44:48.000000000
finished event  30230  endtime =  2020-01-07T20:44:39.000000000
finished event  30231  endtime =  2020-01-07T21:44:25.000000000
finished event  30232  endtime =  2020-01-07T22:44:43.000000000
finished event  30233  endtime =  2020-01-07T23:44:31.000000000
finished event  30234  endtime =  2020-01-08T00:44:22.000000000
finished event  30235  endtime =  2020-01-08T01:44:42.000000000
finished event  30236  endtime =  2020-0

finished event  30534  endtime =  2020-01-20T16:01:14.000000000
finished event  30535  endtime =  2020-01-20T17:01:36.000000000
finished event  30536  endtime =  2020-01-20T18:01:23.000000000
finished event  30537  endtime =  2020-01-20T19:01:10.000000000
finished event  30538  endtime =  2020-01-20T20:01:31.000000000
finished event  30539  endtime =  2020-01-20T21:01:24.000000000
finished event  30540  endtime =  2020-01-20T22:01:13.000000000
finished event  30541  endtime =  2020-01-20T23:01:12.000000000
finished event  30542  endtime =  2020-01-21T00:01:28.000000000
finished event  30543  endtime =  2020-01-21T01:01:18.000000000
finished event  30544  endtime =  2020-01-21T02:01:30.000000000
finished event  30545  endtime =  2020-01-21T03:01:27.000000000
finished event  30546  endtime =  2020-01-21T04:01:18.000000000
finished event  30547  endtime =  2020-01-21T05:01:11.000000000
finished event  30548  endtime =  2020-01-21T06:01:31.000000000
finished event  30549  endtime =  2020-0

finished event  30869  endtime =  2020-02-03T15:00:57.000000000
finished event  30870  endtime =  2020-02-03T16:01:14.000000000
finished event  30871  endtime =  2020-02-03T17:01:01.000000000
finished event  30872  endtime =  2020-02-03T18:01:18.000000000
finished event  30873  endtime =  2020-02-03T19:01:17.000000000
finished event  30874  endtime =  2020-02-03T20:01:24.000000000
finished event  30875  endtime =  2020-02-03T21:01:19.000000000
finished event  30876  endtime =  2020-02-03T22:01:11.000000000
finished event  30877  endtime =  2020-02-03T23:01:01.000000000
finished event  30878  endtime =  2020-02-04T00:01:25.000000000
finished event  30879  endtime =  2020-02-04T01:01:19.000000000
finished event  30880  endtime =  2020-02-04T02:01:11.000000000
finished event  30881  endtime =  2020-02-04T03:00:57.000000000
finished event  30882  endtime =  2020-02-04T04:01:18.000000000
finished event  30883  endtime =  2020-02-04T05:01:02.000000000
finished event  30884  endtime =  2020-0

finished event  31196  endtime =  2020-02-17T06:01:02.000000000
finished event  31197  endtime =  2020-02-17T07:00:54.000000000
finished event  31198  endtime =  2020-02-17T08:01:06.000000000
finished event  31199  endtime =  2020-02-17T09:00:54.000000000
finished event  31200  endtime =  2020-02-17T10:01:07.000000000
finished event  31201  endtime =  2020-02-17T11:00:50.000000000
finished event  31202  endtime =  2020-02-17T12:01:11.000000000
finished event  31203  endtime =  2020-02-17T13:01:11.000000000
finished event  31204  endtime =  2020-02-17T14:01:07.000000000
finished event  31205  endtime =  2020-02-17T15:00:54.000000000
finished event  31206  endtime =  2020-02-17T16:00:44.000000000
finished event  31207  endtime =  2020-02-17T17:01:00.000000000
finished event  31208  endtime =  2020-02-17T18:00:54.000000000
finished event  31209  endtime =  2020-02-17T19:00:44.000000000
finished event  31210  endtime =  2020-02-17T20:01:03.000000000
finished event  31211  endtime =  2020-0

ValueError: arrays must all be same length

In [63]:
i = 0
k = 0
time2 = np.insert(time.values, 0, time.values[0] - 60 * 10**9)
dct_events = {}

while i < len(wind_mag_smooth) - 60:
    wind_mag_1h = wind_mag_smooth[i:i+60]
    nan_idx = np.where(np.isnan(wind_mag_1h))[0]
    if len(nan_idx) > 0:
        i += nan_idx[len(nan_idx) - 1] + 1
        continue
    wind_angle_1h = wind_angle_smooth[i:i+60]
    
    starttime = time2[i:i+60]
    endtime = time.values[i:i+60]
    
    df = pd.DataFrame({ 'windspeed': wind_mag_1h,
                        'windangle': wind_angle_1h,
                        'starttime': starttime,
                        'endtime': endtime})
    dct_events[str(k)] = df
    k += 1
    i += 60
    print('finished event ', k-1, ' endtime = ', endtime[len(endtime) - 1])


finished event  0  endtime =  2015-05-01T00:59:25.000000000
finished event  1  endtime =  2015-05-01T01:59:43.000000000
finished event  2  endtime =  2015-05-01T02:59:47.000000000
finished event  3  endtime =  2015-05-01T03:59:39.000000000
finished event  4  endtime =  2015-05-01T04:59:46.000000000
finished event  5  endtime =  2015-05-01T05:59:24.000000000
finished event  6  endtime =  2015-05-01T06:59:42.000000000
finished event  7  endtime =  2015-05-01T07:59:24.000000000
finished event  8  endtime =  2015-05-01T08:59:41.000000000
finished event  9  endtime =  2015-05-01T09:59:24.000000000
finished event  10  endtime =  2015-05-01T10:59:35.000000000
finished event  11  endtime =  2015-05-01T11:59:43.000000000
finished event  12  endtime =  2015-05-01T12:59:24.000000000
finished event  13  endtime =  2015-05-01T13:59:33.000000000
finished event  14  endtime =  2015-05-01T14:59:50.000000000
finished event  15  endtime =  2015-05-01T15:59:34.000000000
finished event  16  endtime =  201

finished event  357  endtime =  2015-05-15T21:59:18.000000000
finished event  358  endtime =  2015-05-15T22:59:35.000000000
finished event  359  endtime =  2015-05-15T23:59:18.000000000
finished event  360  endtime =  2015-05-16T00:59:31.000000000
finished event  361  endtime =  2015-05-16T01:59:13.000000000
finished event  362  endtime =  2015-05-16T02:59:31.000000000
finished event  363  endtime =  2015-05-16T03:59:17.000000000
finished event  364  endtime =  2015-05-16T04:59:30.000000000
finished event  365  endtime =  2015-05-16T05:59:13.000000000
finished event  366  endtime =  2015-05-16T06:59:27.000000000
finished event  367  endtime =  2015-05-16T07:59:36.000000000
finished event  368  endtime =  2015-05-16T08:59:18.000000000
finished event  369  endtime =  2015-05-16T09:59:27.000000000
finished event  370  endtime =  2015-05-16T10:59:13.000000000
finished event  371  endtime =  2015-05-16T11:59:30.000000000
finished event  372  endtime =  2015-05-16T12:59:40.000000000
finished

finished event  645  endtime =  2015-05-27T21:59:15.000000000
finished event  646  endtime =  2015-05-27T22:59:27.000000000
finished event  647  endtime =  2015-05-27T23:59:10.000000000
finished event  648  endtime =  2015-05-28T00:59:22.000000000
finished event  649  endtime =  2015-05-28T01:59:30.000000000
finished event  650  endtime =  2015-05-28T02:59:14.000000000
finished event  651  endtime =  2015-05-28T03:59:26.000000000
finished event  652  endtime =  2015-05-28T04:59:05.000000000
finished event  653  endtime =  2015-05-28T05:59:22.000000000
finished event  654  endtime =  2015-05-28T06:59:09.000000000
finished event  655  endtime =  2015-05-28T07:59:27.000000000
finished event  656  endtime =  2015-05-28T08:59:19.000000000
finished event  657  endtime =  2015-05-28T09:59:30.000000000
finished event  658  endtime =  2015-05-28T10:59:08.000000000
finished event  659  endtime =  2015-05-28T11:59:22.000000000
finished event  660  endtime =  2015-05-28T12:59:08.000000000
finished

finished event  783  endtime =  2015-06-02T15:59:05.000000000
finished event  784  endtime =  2015-06-02T16:59:18.000000000
finished event  785  endtime =  2015-06-02T17:59:00.000000000
finished event  786  endtime =  2015-06-02T18:59:10.000000000
finished event  787  endtime =  2015-06-02T19:59:22.000000000
finished event  788  endtime =  2015-06-02T20:59:06.000000000
finished event  789  endtime =  2015-06-02T21:59:19.000000000
finished event  790  endtime =  2015-06-02T22:59:04.000000000
finished event  791  endtime =  2015-06-02T23:59:19.000000000
finished event  792  endtime =  2015-06-03T00:59:28.000000000
finished event  793  endtime =  2015-06-03T01:59:01.000000000
finished event  794  endtime =  2015-06-03T02:59:18.000000000
finished event  795  endtime =  2015-06-03T03:59:27.000000000
finished event  796  endtime =  2015-06-03T04:59:00.000000000
finished event  797  endtime =  2015-06-03T05:59:10.000000000
finished event  798  endtime =  2015-06-03T06:59:04.000000000
finished

finished event  1112  endtime =  2015-06-16T08:58:55.000000000
finished event  1113  endtime =  2015-06-16T09:59:10.000000000
finished event  1114  endtime =  2015-06-16T10:59:12.000000000
finished event  1115  endtime =  2015-06-16T11:58:51.000000000
finished event  1116  endtime =  2015-06-16T12:59:08.000000000
finished event  1117  endtime =  2015-06-16T13:58:51.000000000
finished event  1118  endtime =  2015-06-16T14:58:56.000000000
finished event  1119  endtime =  2015-06-16T15:59:08.000000000
finished event  1120  endtime =  2015-06-16T16:58:50.000000000
finished event  1121  endtime =  2015-06-16T17:59:07.000000000
finished event  1122  endtime =  2015-06-16T18:58:50.000000000
finished event  1123  endtime =  2015-06-16T19:59:04.000000000
finished event  1124  endtime =  2015-06-16T20:58:50.000000000
finished event  1125  endtime =  2015-06-16T21:59:05.000000000
finished event  1126  endtime =  2015-06-16T22:59:18.000000000
finished event  1127  endtime =  2015-06-16T23:58:59.00

...

finished event  29850  endtime =  2019-12-22T22:08:48.000000000
finished event  29851  endtime =  2019-12-22T23:08:35.000000000
finished event  29852  endtime =  2019-12-23T00:08:49.000000000
finished event  29853  endtime =  2019-12-23T01:08:35.000000000
finished event  29854  endtime =  2019-12-23T02:08:49.000000000
finished event  29855  endtime =  2019-12-23T03:09:02.000000000
finished event  29856  endtime =  2019-12-23T04:08:56.000000000
finished event  29857  endtime =  2019-12-23T05:08:44.000000000
finished event  29858  endtime =  2019-12-23T06:08:35.000000000
finished event  29859  endtime =  2019-12-23T07:08:58.000000000
finished event  29860  endtime =  2019-12-23T08:08:39.000000000
finished event  29861  endtime =  2019-12-23T09:09:01.000000000
finished event  29862  endtime =  2019-12-23T10:08:53.000000000
finished event  29863  endtime =  2019-12-23T11:08:35.000000000
finished event  29864  endtime =  2019-12-23T12:08:44.000000000
finished event  29865  endtime =  2019-1

finished event  30174  endtime =  2020-01-05T12:17:44.000000000
finished event  30175  endtime =  2020-01-05T13:44:29.000000000
finished event  30176  endtime =  2020-01-05T14:44:50.000000000
finished event  30177  endtime =  2020-01-05T15:44:38.000000000
finished event  30178  endtime =  2020-01-05T16:44:24.000000000
finished event  30179  endtime =  2020-01-05T17:44:41.000000000
finished event  30180  endtime =  2020-01-05T18:44:32.000000000
finished event  30181  endtime =  2020-01-05T19:44:45.000000000
finished event  30182  endtime =  2020-01-05T20:44:31.000000000
finished event  30183  endtime =  2020-01-05T21:44:24.000000000
finished event  30184  endtime =  2020-01-05T22:44:37.000000000
finished event  30185  endtime =  2020-01-05T23:44:50.000000000
finished event  30186  endtime =  2020-01-06T00:44:42.000000000
finished event  30187  endtime =  2020-01-06T01:44:31.000000000
finished event  30188  endtime =  2020-01-06T02:44:24.000000000
finished event  30189  endtime =  2020-0

finished event  30520  endtime =  2020-01-20T02:01:31.000000000
finished event  30521  endtime =  2020-01-20T03:01:20.000000000
finished event  30522  endtime =  2020-01-20T04:01:29.000000000
finished event  30523  endtime =  2020-01-20T05:01:28.000000000
finished event  30524  endtime =  2020-01-20T06:01:14.000000000
finished event  30525  endtime =  2020-01-20T07:01:35.000000000
finished event  30526  endtime =  2020-01-20T08:01:19.000000000
finished event  30527  endtime =  2020-01-20T09:01:10.000000000
finished event  30528  endtime =  2020-01-20T10:01:23.000000000
finished event  30529  endtime =  2020-01-20T11:01:10.000000000
finished event  30530  endtime =  2020-01-20T12:01:32.000000000
finished event  30531  endtime =  2020-01-20T13:01:19.000000000
finished event  30532  endtime =  2020-01-20T14:01:09.000000000
finished event  30533  endtime =  2020-01-20T15:01:26.000000000
finished event  30534  endtime =  2020-01-20T16:01:14.000000000
finished event  30535  endtime =  2020-0

finished event  30850  endtime =  2020-02-02T20:01:03.000000000
finished event  30851  endtime =  2020-02-02T21:01:24.000000000
finished event  30852  endtime =  2020-02-02T22:01:06.000000000
finished event  30853  endtime =  2020-02-02T23:00:58.000000000
finished event  30854  endtime =  2020-02-03T00:01:10.000000000
finished event  30855  endtime =  2020-02-03T01:01:01.000000000
finished event  30856  endtime =  2020-02-03T02:01:20.000000000
finished event  30857  endtime =  2020-02-03T03:01:13.000000000
finished event  30858  endtime =  2020-02-03T04:01:02.000000000
finished event  30859  endtime =  2020-02-03T05:00:57.000000000
finished event  30860  endtime =  2020-02-03T06:01:24.000000000
finished event  30861  endtime =  2020-02-03T07:01:24.000000000
finished event  30862  endtime =  2020-02-03T08:01:10.000000000
finished event  30863  endtime =  2020-02-03T09:00:57.000000000
finished event  30864  endtime =  2020-02-03T10:01:15.000000000
finished event  30865  endtime =  2020-0

finished event  31182  endtime =  2020-02-16T16:00:59.000000000
finished event  31183  endtime =  2020-02-16T17:00:45.000000000
finished event  31184  endtime =  2020-02-16T18:01:04.000000000
finished event  31185  endtime =  2020-02-16T19:00:54.000000000
finished event  31186  endtime =  2020-02-16T20:01:09.000000000
finished event  31187  endtime =  2020-02-16T21:00:55.000000000
finished event  31188  endtime =  2020-02-16T22:00:45.000000000
finished event  31189  endtime =  2020-02-16T23:01:04.000000000
finished event  31190  endtime =  2020-02-17T00:00:56.000000000
finished event  31191  endtime =  2020-02-17T01:00:46.000000000
finished event  31192  endtime =  2020-02-17T02:00:58.000000000
finished event  31193  endtime =  2020-02-17T03:00:45.000000000
finished event  31194  endtime =  2020-02-17T04:01:03.000000000
finished event  31195  endtime =  2020-02-17T05:00:49.000000000
finished event  31196  endtime =  2020-02-17T06:01:02.000000000
finished event  31197  endtime =  2020-0

In [3]:
for key in dct_events:
    dct_events[key].to_csv('wind_data_offshore_events/offshore_' + str(key) + '.csv')

NameError: name 'dct_events' is not defined

In [2]:
import numpy as np
import json
import os
from matplotlib import pyplot as plt
import matplotlib.dates as mdates
from obspy import read,Stream, Trace
from obspy.core import UTCDateTime
import math as M
from matplotlib import mlab
from matplotlib.colors import Normalize
import requests
from lxml import html
from scipy import signal
from scipy import interpolate
from scipy import stats
import matplotlib.colors as colors
import datetime
from scipy import signal
import requests
import urllib
import datetime
import time as tm
import pandas as pd
import multiprocessing as mp
import function_lib as lib
import function_lib_mp as libmp
import math
import pickle
import matplotlib

# read file containing the wind events
wind_dct = {}
for file in os.listdir('test/'):
    wind_dct[file.split('_')[1].split('.')[0]] = pd.read_csv('test/' + file )
    
#convert starttime and endtime to datetime objects
for key in wind_dct:
    for i in range(len(wind_dct[key])):
        pd.set_option('mode.chained_assignment','warn')
        wind_dct[key].starttime[i] = datetime.datetime.fromisoformat(wind_dct[key].starttime[i])
        wind_dct[key].endtime[i] = datetime.datetime.fromisoformat(wind_dct[key].endtime[i])

C:\Users\fschwock\AppData\Local\Continuum\anaconda3\envs\obspy\lib\site-packages\ipykernel_launcher.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\fschwock\AppData\Local\Continuum\anaconda3\envs\obspy\lib\site-packages\ipykernel_launcher.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [3]:
import ooi_data_processing_library as ooilib
import ooi_data_processing_library_old as ooilib_old
import time

In [6]:
cnt = 0
t_start = time.time()

for key in wind_dct:
    start = wind_dct[key].starttime[0]
    end = wind_dct[key].endtime[len(wind_dct[key].endtime) - 1]
    
    t, f, specgram = ooilib_old.compute_spectrogram_mp(start, end, 60, node='/LJ01C', avg_time=1)
    if len(specgram) != 0:
        ooilib_old.visualize_spectrogram(specgram, t, f/1000, plot_spec=False, save_spec=True,
                                     filename='results/offshore_spec_wind/' + key + '.png',
                                     title='offshore #' + key, ylabel='freq [kHz]', xlabel='time')
    else: continue

    start_end = np.transpose(np.array([wind_dct[key].starttime, wind_dct[key].endtime]))
    f, psds = ooilib_old.compute_psd_welch_mp(start, end, start_end, node='/LJ01C')
    
    if not os.path.exists('results/offshore_PSD_wind/' + key):
        os.makedirs('results/offshore_PSD_wind/' + key)
                          
    ws = wind_dct[key].windspeed
    wa = wind_dct[key].windangle
    for i in range(len(psds)):
        ooilib_old.save_psd(psds[i], f=f, filename='results/offshore_PSD_wind/' + key + '/' + str(i) + '.json',
                       ancillary_data=[ws, wa], ancillary_data_label=['windspeed', 'windangle'])
    
    cnt += 1
    print('PSD ', key, ' finished; ', cnt/len(wind_dct), ' %')
    
print(time.time() - t_start)

PSD  5910  finished;  0.5  %
PSD  5911  finished;  1.0  %
1328.298394203186


In [5]:
cnt = 0
t_start = time.time()

for key in wind_dct:
    start = wind_dct[key].starttime[0]
    end = wind_dct[key].endtime[len(wind_dct[key].endtime) - 1]
    ooi = ooilib.OOIHyrophoneData()
    ooi.get_acoustic_data_mp(start, end, node='/LJ01C')
    ooi.compute_spectrogram_mp(avg_time=1)
    if ooi.spectrogram != None:
        ooi.spectrogram.freq /= 1000
        ooi.spectrogram.visualize(plot_spec=False, save_spec=True,
                      filename='results/offshore_spec_wind/' + key + '.png',
                      title='offshore #' + key, ylabel='freq [kHz]', xlabel='time', dpi=16)
    else: continue

    start_end = np.transpose(np.array([wind_dct[key].starttime, wind_dct[key].endtime]))
    ooi.compute_psd_welch_mp(start_end)
    
    if not os.path.exists('results/offshore_PSD_wind/' + key):
        os.makedirs('results/offshore_PSD_wind/' + key)
                          
    ws = wind_dct[key].windspeed
    wa = wind_dct[key].windangle
    for psd in ooi.psd_list:
        psd.save(filename='results/offshore_PSD_wind/' + key + '/' + str(i) + '.json',
                 ancillary_data=[ws, wa], ancillary_data_label=['windspeed', 'windangle'])
    
    cnt += 1
    print('PSD ', key, ' finished; ', cnt/len(wind_dct), ' %')
    
    print(time.time() - t_start)

PSD  5910  finished;  0.5  %
525.4688155651093
PSD  5911  finished;  1.0  %
1054.0597441196442


In [6]:
ooi.data == None

False